2/27/25 - I'm just going to redo the wavelet code.  
1. So, this will make both uncorrected and corrected wavelets, and save them.  
2. And plot_wavelets.ipynb will plot them.  
3. Then, in wavelet_differences.ipynb, I should load in the wavelets and plot them against each other.

In [2]:
import os
import sys
print(sys.path)
sys.path.append("C:/Users/jz421/Desktop/GlobalLocal/IEEG_Pipelines/") #need to do this cuz otherwise ieeg isn't added to path...

# Get the absolute path to the directory containing the current script
# For GlobalLocal/src/analysis/preproc/make_epoched_data.py, this is GlobalLocal/src/analysis/preproc
try:
    # This will work if running as a .py script
    current_file_path = os.path.abspath(__file__)
    current_script_dir = os.path.dirname(current_file_path)
except NameError:
    # This will be executed if __file__ is not defined (e.g., in a Jupyter Notebook)
    # os.getcwd() often gives the directory of the notebook,
    # or the directory from which the Jupyter server was started.
    current_script_dir = os.getcwd()

# Navigate up three levels to get to the 'GlobalLocal' directory
project_root = os.path.abspath(os.path.join(current_script_dir, '..', '..', '..'))

# Add the 'GlobalLocal' directory to sys.path if it's not already there
if project_root not in sys.path:
    sys.path.insert(0, project_root) # insert at the beginning to prioritize it

import mne.time_frequency
import mne
from ieeg.io import get_data, raw_from_layout
from ieeg.navigate import trial_ieeg, channel_outlier_marker, crop_empty_data, outliers_to_nan
from ieeg.calc.scaling import rescale

from ieeg.timefreq.utils import wavelet_scaleogram, crop_pad
import numpy as np
from src.analysis.utils.general_utils import get_good_data
from src.analysis.spec.wavelet_functions import get_uncorrected_wavelets

['C:\\Users\\jz421\\Desktop\\GlobalLocal\\IEEG_Pipelines', 'c:\\Users\\jz421\\AppData\\Local\\anaconda3\\envs\\ieeg\\python311.zip', 'c:\\Users\\jz421\\AppData\\Local\\anaconda3\\envs\\ieeg\\DLLs', 'c:\\Users\\jz421\\AppData\\Local\\anaconda3\\envs\\ieeg\\Lib', 'c:\\Users\\jz421\\AppData\\Local\\anaconda3\\envs\\ieeg', '', 'C:\\Users\\jz421\\AppData\\Roaming\\Python\\Python311\\site-packages', 'C:\\Users\\jz421\\AppData\\Roaming\\Python\\Python311\\site-packages\\win32', 'C:\\Users\\jz421\\AppData\\Roaming\\Python\\Python311\\site-packages\\win32\\lib', 'C:\\Users\\jz421\\AppData\\Roaming\\Python\\Python311\\site-packages\\Pythonwin', 'c:\\Users\\jz421\\AppData\\Local\\anaconda3\\envs\\ieeg\\Lib\\site-packages', 'c:\\Users\\jz421\\AppData\\Local\\anaconda3\\envs\\ieeg\\Lib\\site-packages\\win32', 'c:\\Users\\jz421\\AppData\\Local\\anaconda3\\envs\\ieeg\\Lib\\site-packages\\win32\\lib', 'c:\\Users\\jz421\\AppData\\Local\\anaconda3\\envs\\ieeg\\Lib\\site-packages\\Pythonwin']


In [3]:
HOME = os.path.expanduser("~")

# get box directory depending on OS
if os.name == 'nt': # windows
    LAB_root = os.path.join(HOME, "Box", "CoganLab")
else: # mac
    LAB_root = os.path.join(HOME, "Library", "CloudStorage", "Box-Box", "CoganLab")

layout = get_data("GlobalLocal", root=LAB_root)

# let's make a dictionary where the keys are output names and the values are lists of corresponding events
output_names_and_events_dict = {}
# output_names_and_events_dict['Stimulus_c25and75_fixationCrossBase_0.5sec'] = ["Stimulus/c75.0", "Stimulus/c25.0"]
# output_names_and_events_dict['Stimulus_i25and75_fixationCrossBase_0.5sec'] = ["Stimulus/i75.0", "Stimulus/i25.0"]
# output_names_and_events_dict['Stimulus_s25and75_fixationCrossBase_0.5sec'] = ['Stimulus/i75.0/s25.0', 'Stimulus/i25.0/s75.0', 'Stimulus/c75.0/s25.0', 'Stimulus/c25.0/s75.0']
# output_names_and_events_dict['Stimulus_r25and75_fixationCrossBase_0.5sec'] = ['Stimulus/i75.0/r25.0', 'Stimulus/i25.0/r75.0', 'Stimulus/c75.0/r25.0', 'Stimulus/c25.0/r75.0']
output_names_and_events_dict['Stimulus_fixationCrossBase_0.5sec'] = ["Stimulus"]

baseline_times = [-0.5, 0]
signal_times = [-0.5, 1.5]

subjects = ['D0057','D0059', 'D0063', 'D0065', 'D0069', 'D0071', 'D0077', 'D0090', 'D0094', 'D0100', 'D0102', 'D0103', 'D0107A', 'D0110', 'D0116', 'D0117', 'D0121']

for sub in subjects:
    # load in good data so we can use it for gettin bad channels and getting filenames
    good = get_good_data(sub, layout)

    ## epoching and trial outlier removal

    save_dir = os.path.join(layout.root, 'derivatives', 'spec', 'wavelet', sub)
    if not os.path.exists(save_dir):
            os.makedirs(save_dir)

    # make stimulus baseline EpochsTFR
    base = get_uncorrected_wavelets(sub, layout, events=["Stimulus"], times=baseline_times)

    # make signal wavelets
    for output_name, events in output_names_and_events_dict.items():
        spec = get_uncorrected_wavelets(sub, layout, events, signal_times)
        spec_rescaled = rescale(spec, base, copy=True, mode='ratio').average(
            lambda x: np.nanmean(x, axis=0), copy=True)
        spec_rescaled._data = np.log10(spec_rescaled._data) * 20 # convert to dB
        fnames = [os.path.relpath(f, layout.root) for f in good.filenames]
        spec_rescaled.info['subject_info']['files'] = tuple(fnames)
        spec_rescaled.info['bads'] = good.info['bads']

        rescaled_filename = os.path.join(save_dir, f'{output_name}_rescaled-tfr.h5')
        uncorrected_filename = os.path.join(save_dir, f'{output_name}_uncorrected-tfr.h5')

        mne.time_frequency.write_tfrs(rescaled_filename, spec_rescaled, overwrite=True)
        mne.time_frequency.write_tfrs(uncorrected_filename, spec, overwrite=True)
        
        spec_rescaled.save(os.path.join(save_dir, f'{output_name}_rescaled-avg.fif'), overwrite=True)
        spec.save(os.path.join(save_dir, f'{output_name}_uncorrected-avg.fif'), overwrite=True)

Extracting EDF parameters from C:\Users\jz421\Box\CoganLab\BIDS-1.1_GlobalLocal\BIDS\derivatives\clean\sub-D0057\ieeg\sub-D0057_task-GlobalLocal_acq-01_run-01_desc-clean_ieeg.edf...
EDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading events from C:\Users\jz421\Box\CoganLab\BIDS-1.1_GlobalLocal\BIDS\derivatives\clean\sub-D0057\ieeg\sub-D0057_task-GlobalLocal_acq-01_run-01_desc-clean_events.tsv.
Reading channel info from C:\Users\jz421\Box\CoganLab\BIDS-1.1_GlobalLocal\BIDS\derivatives\clean\sub-D0057\ieeg\sub-D0057_task-GlobalLocal_acq-01_run-01_desc-clean_channels.tsv.
Reading electrode coords from C:\Users\jz421\Box\CoganLab\BIDS-1.1_GlobalLocal\BIDS\derivatives\clean\sub-D0057\ieeg\sub-D0057_acq-01_space-ACPC_electrodes.tsv.
Extracting EDF parameters from C:\Users\jz421\Box\CoganLab\BIDS-1.1_GlobalLocal\BIDS\derivatives\clean\sub-D0057\ieeg\sub-D0057_task-GlobalLocal_acq-01_run-02_desc-clean_ieeg.edf...
EDF file detected
Setting channel info str

C:\Users\jz421\Desktop\GlobalLocal\IEEG_Pipelines\ieeg\io.py:113: RuntimeWarning: The number of channels in the channels.tsv sidecar file (179) does not match the number of channels in the raw data file (178). Will not try to set channel names.
  new_raw = read_raw_bids(bids_path=BIDS_path, verbose=verbose)
C:\Users\jz421\Desktop\GlobalLocal\IEEG_Pipelines\ieeg\io.py:113: RuntimeWarning: Cannot set channel type for the following channels, as they are missing in the raw data: Trigger
  new_raw = read_raw_bids(bids_path=BIDS_path, verbose=verbose)


Reading events from C:\Users\jz421\Box\CoganLab\BIDS-1.1_GlobalLocal\BIDS\derivatives\clean\sub-D0057\ieeg\sub-D0057_task-GlobalLocal_acq-01_run-02_desc-clean_events.tsv.
Reading channel info from C:\Users\jz421\Box\CoganLab\BIDS-1.1_GlobalLocal\BIDS\derivatives\clean\sub-D0057\ieeg\sub-D0057_task-GlobalLocal_acq-01_run-02_desc-clean_channels.tsv.
Reading electrode coords from C:\Users\jz421\Box\CoganLab\BIDS-1.1_GlobalLocal\BIDS\derivatives\clean\sub-D0057\ieeg\sub-D0057_acq-01_space-ACPC_electrodes.tsv.


C:\Users\jz421\Desktop\GlobalLocal\IEEG_Pipelines\ieeg\io.py:113: RuntimeWarning: Omitted 228 annotation(s) that were outside data range.
  new_raw = read_raw_bids(bids_path=BIDS_path, verbose=verbose)
C:\Users\jz421\Desktop\GlobalLocal\IEEG_Pipelines\ieeg\io.py:113: RuntimeWarning: The number of channels in the channels.tsv sidecar file (179) does not match the number of channels in the raw data file (178). Will not try to set channel names.
  new_raw = read_raw_bids(bids_path=BIDS_path, verbose=verbose)
C:\Users\jz421\Desktop\GlobalLocal\IEEG_Pipelines\ieeg\io.py:113: RuntimeWarning: Cannot set channel type for the following channels, as they are missing in the raw data: Trigger
  new_raw = read_raw_bids(bids_path=BIDS_path, verbose=verbose)


Extracting EDF parameters from C:\Users\jz421\Box\CoganLab\BIDS-1.1_GlobalLocal\BIDS\derivatives\clean\sub-D0057\ieeg\sub-D0057_task-GlobalLocal_acq-01_run-03_desc-clean_ieeg.edf...
EDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading events from C:\Users\jz421\Box\CoganLab\BIDS-1.1_GlobalLocal\BIDS\derivatives\clean\sub-D0057\ieeg\sub-D0057_task-GlobalLocal_acq-01_run-03_desc-clean_events.tsv.
Reading channel info from C:\Users\jz421\Box\CoganLab\BIDS-1.1_GlobalLocal\BIDS\derivatives\clean\sub-D0057\ieeg\sub-D0057_task-GlobalLocal_acq-01_run-03_desc-clean_channels.tsv.
Reading electrode coords from C:\Users\jz421\Box\CoganLab\BIDS-1.1_GlobalLocal\BIDS\derivatives\clean\sub-D0057\ieeg\sub-D0057_acq-01_space-ACPC_electrodes.tsv.
Extracting EDF parameters from C:\Users\jz421\Box\CoganLab\BIDS-1.1_GlobalLocal\BIDS\derivatives\clean\sub-D0057\ieeg\sub-D0057_task-GlobalLocal_acq-01_run-04_desc-clean_ieeg.edf...
EDF file detected
Setting channel info str

...

c:\Users\jz421\Desktop\GlobalLocal\src\analysis\spec\wavelet_functions.py:130: RuntimeWarning: Concatenation of Annotations within Epochs is not supported yet. All annotations will be dropped.
  all_trials = mne.concatenate_epochs(all_trials_list)


Not setting metadata
448 matching events found
No baseline correction applied
Data is self data: True


[Parallel(n_jobs=1)]: Done   1 tasks      | elapsed:    9.1s
[Parallel(n_jobs=1)]: Done   4 tasks      | elapsed:   37.0s
[Parallel(n_jobs=1)]: Done   7 tasks      | elapsed:  1.1min
[Parallel(n_jobs=1)]: Done  12 tasks      | elapsed:  1.9min
[Parallel(n_jobs=1)]: Done  17 tasks      | elapsed:  2.7min
[Parallel(n_jobs=1)]: Done  24 tasks      | elapsed:  3.8min
[Parallel(n_jobs=1)]: Done  31 tasks      | elapsed:  4.9min
[Parallel(n_jobs=1)]: Done  40 tasks      | elapsed:  6.3min
[Parallel(n_jobs=1)]: Done  49 tasks      | elapsed:  7.6min
[Parallel(n_jobs=1)]: Done  60 tasks      | elapsed:  9.4min
[Parallel(n_jobs=1)]: Done  71 tasks      | elapsed: 11.1min
[Parallel(n_jobs=1)]: Done  84 tasks      | elapsed: 13.1min
[Parallel(n_jobs=1)]: Done  97 tasks      | elapsed: 15.1min
[Parallel(n_jobs=1)]: Done 112 tasks      | elapsed: 17.5min
[Parallel(n_jobs=1)]: Done 127 tasks      | elapsed: 20.0min
[Parallel(n_jobs=1)]: Done 144 tasks      | elapsed: 22.6min
[Parallel(n_jobs=1)]: Do

Applying baseline correction (mode: ratio)


C:\Users\jz421\AppData\Local\Temp\ipykernel_23328\4231187139.py:53: RuntimeWarning: This filename (C:\Users\jz421\Box\CoganLab\BIDS-1.1_GlobalLocal\BIDS\derivatives\spec\wavelet\D0121\Stimulus_fixationCrossBase_0.5sec_rescaled-avg.fif) does not conform to MNE naming conventions. All time-frequency object files should end with .h5 or .hdf5
  spec_rescaled.save(os.path.join(save_dir, f'{output_name}_rescaled-avg.fif'), overwrite=True)
C:\Users\jz421\AppData\Local\Temp\ipykernel_23328\4231187139.py:54: RuntimeWarning: This filename (C:\Users\jz421\Box\CoganLab\BIDS-1.1_GlobalLocal\BIDS\derivatives\spec\wavelet\D0121\Stimulus_fixationCrossBase_0.5sec_uncorrected-avg.fif) does not conform to MNE naming conventions. All time-frequency object files should end with .h5 or .hdf5
  spec.save(os.path.join(save_dir, f'{output_name}_uncorrected-avg.fif'), overwrite=True)
